In [ ]:
!curl --location --remote-name --remote-header-name \
    http://ftp.eea.europa.eu/www/eprtr/v17/E-PRTR_database_v17_xls.zip

In [ ]:
!unzip E-PRTR_database_v17_xls.zip 'Pollutant releases.xlsx'

In [ ]:
import pandas

pollutant_releases = pandas.read_excel('Pollutant releases.xlsx')
pollutant_releases.head()

In [ ]:
import geopandas

# http://geopandas.org/gallery/create_geopandas_from_pandas.html
pollutant_releases_geo = geopandas.GeoDataFrame(
    pollutant_releases,
    geometry=geopandas.points_from_xy(
        pollutant_releases['Long'],
        pollutant_releases['Lat'],
    ),
)
pollutant_releases_geo.geometry.head()

In [ ]:
world = geopandas.read_file(geopandas.datasets.get_path('naturalearth_lowres'))

In [ ]:
ax = world[(world.continent == 'Europe')].plot(
    edgecolor='black',
    color='white',
    figsize=(20, 12),
)
ax.set_xlim(-28, 32)
ax.set_ylim(32, 75)
ax.set_title('E-PRTR_database_v17_xls.zip / Pollutant releases.xlsx')
pollutant_releases_geo.plot(ax=ax, markersize=0.1);

In [ ]:
european_facilities = geopandas.GeoDataFrame(pollutant_releases_geo[
    (pollutant_releases_geo.Long > -28)
    & (pollutant_releases_geo.Long < 32)
    & (pollutant_releases_geo.Lat > 32)
    & (pollutant_releases_geo.Lat < 75)
].groupby('FacilityID').first())

In [ ]:
import geoplot

ax = geoplot.kdeplot(
    european_facilities,
    clip=world.geometry,
    shade=True,
    cmap='Reds',
    projection=geoplot.crs.AlbersEqualArea(),
    figsize=(24, 16),
)
ax.set_title('E-PRTR_database_v17_xls.zip / Pollutant releases.xlsx / kdeplot')